# CONTACT MAPS CALCULATION AND ANALYSIS

In [1]:
import pandas as pd
import structure_validation
import structural_analysis
import contact_maps
import importlib
import scipy.stats as stats

In [2]:
df_allsp = pd.read_csv("/cluster/gjb_lab/2394007/varalign_runs/varalign_bio_units4/.varalign/prointvar_analysis_data/anks_final_aln.sto_prointvar_structure_table_with_validation.csv") # STRUCTURAL DATA TABLE
aln_in = "/cluster/gjb_lab/2394007/varalign_runs/varalign_edited_code2/anks_final_aln.sto" # MSA
aln_fmt = "stockholm" # MSA FORMAT

2021-05-14 11:06:42,324 - WARNING - /cluster/gjb_lab/2394007/miniconda/envs/myenv/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (1,14,15,18,19,25,26,28,29,31,33,41,42,43,44,45,46,47,48,51,52,63,64,65,67,69,71,75,76,77,91,95,113,115,118,119,122,123,128,129,132,133,142,143,149,151,153,155,157,161,163,169,206,208,213,214,230,231,232,233,234,243,274,278,280,281,284,300,301,304,308,310) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
 


In [3]:
df_allsp_rsrz_filt = structure_validation.filter_rsrz_rscc(df_allsp) # FILTERS STRUCTURAL TABLE SO WE KEEP HIGH QUALITY RESIDUES MEETING OUR RSCC AND RSRZ THRESHOLDS
cons_cols_allsp = structural_analysis.get_cons_cols(aln_in, aln_fmt) # GETS CONSENSUS COLUMNS FROM MSA (OCCUPANCY > 0.5)
df_rf = contact_maps.format_df(df_allsp_rsrz_filt, cons_cols_allsp) # FORMATS STRUCTURAL TABLE FOR FOLLOW-UP ANALYSIS

cons_cols_eq = contact_maps.get_cons_cols_eq(cons_cols_allsp) # EQUIVALENCE BETWEEN CONSENSUS ALIGNMENT COLUMN NUMBERS AND DOMAIN POSITIONS (1-33)
df_cols_eq = contact_maps.get_df_cols_eq(df_rf)

2021-05-14 11:06:45,459 - WARNING - /cluster/gjb_lab/2394007/miniconda/envs/myenv/lib/python3.7/site-packages/pandas/core/generic.py:5208: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
 
2021-05-14 11:06:45,831 - WARNING - /cluster/home/2394007/contact_maps.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df2_cons["Alignment_column_cons_A"] = df2_cons.Alignment_column_A.map(cons_cols_eq)
 
2021-05-14 11:06:45,839 - WARNING - /cluster/home/2394007/contact_maps.py:26: SettingWithCopyWarni

## INTRA-ANK REPEAT INTERACTIONS

In [4]:
intra_res_occ = contact_maps.get_intra_cons_occ(df_rf, cons_cols_eq) # GETS COVERAGE OF EACH INTRA-REPEAT POSITION PAIR IN OUR STRUCTURAL DATASET

The dataframe contains information of:
27017 residues, 10586 of which are unique
174 PDB structures
72 different proteins
382 unique repeats


In [6]:
intra = contact_maps.get_intra_cons(df_rf, cons_cols_eq, t = 0) # CALCULATES ABSOLUTE FREQUENCY OF INTRA-REPEAT CONTACTS
intra_norm = contact_maps.normalize_contacts(intra, intra_res_occ) # NORMALISES CONTACT MAP BY POSITION PAIR COVERAGE IN DATASET

In [7]:
contact_maps.plot_intra_cons(intra_norm, "viridis")

### INTRA-ANK CONTACTS BETWEEN RESIDUES FURTHER APPART THAN 5 RESIDUES

In [8]:
intra_t5 = contact_maps.get_intra_cons(df_rf, cons_cols_eq, t = 5) # ONLY PAIRS OF POSITIONS FURTHER AWAY THAN 5 POSITIONS FROM EACH OTHER
intra_norm_t5 = contact_maps.normalize_contacts(intra_t5, intra_res_occ) # NORMALISATION

In [9]:
contact_maps.plot_intra_cons(intra_norm_t5, "viridis")

In [10]:
occ_intra = contact_maps.get_tot_occ_res(intra_res_occ, len(intra), contact_map = "intra", t = 5) # STRUCTURAL COVERAGE PER POSITION
cons_intra = contact_maps.get_tot_cons_res(intra, contact_map = "intra", t = 5) # TOTAL NUMBER OF CONTACTS PER POSITION
enrichment_df_intra = contact_maps.get_OR_from_cons(cons_intra, occ_intra) # CALCULATES ENRICHMENT SCORES IN INTRA-REPEAT CONTACTS, P-VALUE, AND 95% CI FOR ENRICHMENT SCORE
enrichment_df_intra = structural_analysis.add_miss_class(enrichment_df_intra) # ADDS MISSENSE ENRICHMENT CLASS

### ENRICHMENT IN INTRA-REPEAT CONTACTS

In [11]:
cmd_cons = enrichment_df_intra[enrichment_df_intra.color_class == "royalblue"].contacts.sum()
cmd_occ = enrichment_df_intra[enrichment_df_intra.color_class == "royalblue"].occ.sum()
rest_cons = enrichment_df_intra[enrichment_df_intra.color_class != "royalblue"].contacts.sum()
rest_occ = enrichment_df_intra[enrichment_df_intra.color_class != "royalblue"].occ.sum()

In [15]:
oddsr, pval = stats.fisher_exact([[cmd_cons, rest_cons], [cmd_occ, rest_occ]]) # CMDs ARE ENRICHED IN INTRA-REPEAT CONTACTS RELATIVE TO REST OF ANK POSITIONS
oddsr, pval

(2.774861586219705, 0.0)

In [16]:
contact_maps.plot_cons_enrichment(enrichment_df_intra, class_col = "class", color_col = "color_class")

## INTER-ANK REPEAT INTERACTIONS

In [17]:
inter_res_occ = contact_maps.get_inter_cons_occ(df_rf, cons_cols_eq)
inter = contact_maps.get_inter_cons(df_rf, cons_cols_eq, df_cols_eq)
inter_norm = contact_maps.normalize_contacts(inter, inter_res_occ)

The dataframe contains information of:
27017 residues, 10586 of which are unique
174 PDB structures
72 different proteins
382 unique repeats
310 pairs of ARs were used


In [28]:
contact_maps.plot_inter_cons(inter_norm, "viridis")

### ENRICHMENT IN INTER-REPEAT CONTACTS

In [19]:
occ_inter = contact_maps.get_tot_occ_res(inter_res_occ, len(inter), contact_map = "inter", t = 0) # CALCULATES THE ABSOLUTE STRUCTURAL COVERAGE PER DOMAIN POSITION
cons_inter = contact_maps.get_tot_cons_res(inter, contact_map = "inter", t = 0) # CALCULATES THE ABSOLUTE NUMBER OF CONTACTS PER DOMAIN POSITION
enrichment_df_inter = contact_maps.get_OR_from_cons(cons_inter, occ_inter) # CALCULATES OR, LOG(OR), P-VALUE AND 95% CI FOR THE ENRICHMENT IN CONTACTS
enrichment_df_inter = structural_analysis.add_miss_class(enrichment_df_inter) # ADDS MISSENSE ENRICHMENT CLASS

In [20]:
enrichment_df_inter.head()

occ  contacts  oddsratio  log_oddsratio         pvalue   ci_dist class  \
1  16251     378.0   0.456315      -0.784573   1.440518e-64  0.102700   UMD   
2  17153     531.0   0.609702      -0.494786   4.659604e-33  0.087221  None   
3  17465    1067.0   1.226796       0.204406   6.244718e-10  0.063024   UMD   
4  17847    1252.0   1.417546       0.348927   6.903973e-29  0.058620   CME   
5  18023    1680.0   1.913965       0.649177  2.589682e-115  0.051526   CME   

  color_class  
1   firebrick  
2        grey  
3   firebrick  
4       green  
5       green

In [21]:
cmd_inter_cons = enrichment_df_inter[enrichment_df_inter.color_class == "royalblue"].contacts.sum()
cmd_inter_occ = enrichment_df_inter[enrichment_df_inter.color_class == "royalblue"].occ.sum()
rest_inter_cons = enrichment_df_inter.contacts.sum() - cmd_inter_cons
rest_inter_occ = enrichment_df_inter.occ.sum() - cmd_inter_occ

In [23]:
oddsr, pval = stats.fisher_exact([[cmd_inter_cons, rest_inter_cons], [cmd_inter_occ, rest_inter_occ]]) # CMDs ARE NOT ENRICHED IN INTER-REPEAT CONTACTS
oddsr, pval

(0.8525985438808474, 5.0304787038892e-20)

In [24]:
contact_maps.plot_cons_enrichment(enrichment_df_inter, contact_map = "Inter", class_col = "class", color_col = "color_class")